In [1]:
#Import our libraries
import time
import requests
import json
import xml.etree.ElementTree as ET  # for parsing XML
import xmltodict
import pandas as pd
import csv
import base64 
import sqlalchemy

# Step 1: Get the authentication token and instance key 

In [2]:
#Our endpoint
url="https://service5.ultipro.com/services/BIDataService"

#The below headers variable specifies that we are sending the request to a SOAP API
headers = {"content-type": "application/soap+xml"}

In [3]:
body = """ <s:Envelope xmlns:s="http://www.w3.org/2003/05/soap-envelope" xmlns:a="http://www.w3.org/2005/08/addressing">

  <s:Header>

<a:Action s:mustUnderstand="1">http://www.ultipro.com/dataservices/bidata/2/IBIDataService/LogOn</a:Action>

<a:To s:mustUnderstand="1">https://servicehost/services/BiDataService</a:To>

</s:Header>

  <s:Body>

  <LogOn xmlns="http://www.ultipro.com/dataservices/bidata/2">

  <logOnRequest xmlns:i="http://www.w3.org/2001/XMLSchema-instance">

<UserName>BI_Data</UserName>

<Password>SG]xJZ4}/^G!lX!G!#pk5==$HoKo@M|4;O?=$?x3k(|1gd6g_N</Password>

<ClientAccessKey>PLAB4</ClientAccessKey>

<UserAccessKey>ED5P34000010</UserAccessKey>

</logOnRequest>

</LogOn>

</s:Body>

</s:Envelope> """

In [4]:
#View the response
response = requests.post(url, headers=headers, data=body)
print (response)
print (response.text)

<Response [200]>
<s:Envelope xmlns:s="http://www.w3.org/2003/05/soap-envelope" xmlns:a="http://www.w3.org/2005/08/addressing"><s:Header><a:Action s:mustUnderstand="1">http://www.ultipro.com/dataservices/bidata/2/IBIDataService/LogOnResponse</a:Action></s:Header><s:Body><LogOnResponse xmlns="http://www.ultipro.com/dataservices/bidata/2"><LogOnResult xmlns:i="http://www.w3.org/2001/XMLSchema-instance"><ServiceId>dae1578e-72df-4278-9bb8-4cf1bb5b3ce9</ServiceId><ClientAccessKey>PLAB4</ClientAccessKey><Token>800aa77a-55c2-4338-ab67-d2c17df0cbaf</Token><Status>Ok</Status><StatusMessage i:nil="true"/><InstanceKey>2d046e0e-bbc4-448b-a8aa-67653ac41d8a</InstanceKey></LogOnResult></LogOnResponse></s:Body></s:Envelope>


Now, iterate through the response to get the token, service_id, and instance key

In [5]:
#Write the response to a file
open("file.xml", "w").write(response.text)

699

In [6]:
#Open the file as an ElementTree object
tree = ET.parse('file.xml')
root = tree.getroot()

In [7]:
#Show all the elements in the tree
[elem.tag for elem in root.iter()]

['{http://www.w3.org/2003/05/soap-envelope}Envelope',
 '{http://www.w3.org/2003/05/soap-envelope}Header',
 '{http://www.w3.org/2005/08/addressing}Action',
 '{http://www.w3.org/2003/05/soap-envelope}Body',
 '{http://www.ultipro.com/dataservices/bidata/2}LogOnResponse',
 '{http://www.ultipro.com/dataservices/bidata/2}LogOnResult',
 '{http://www.ultipro.com/dataservices/bidata/2}ServiceId',
 '{http://www.ultipro.com/dataservices/bidata/2}ClientAccessKey',
 '{http://www.ultipro.com/dataservices/bidata/2}Token',
 '{http://www.ultipro.com/dataservices/bidata/2}Status',
 '{http://www.ultipro.com/dataservices/bidata/2}StatusMessage',
 '{http://www.ultipro.com/dataservices/bidata/2}InstanceKey']

In [8]:
#Get the token from the "Token" element in the tree
for each in root.iter('{http://www.ultipro.com/dataservices/bidata/2}Token'):
    token = each.text

In [9]:
#Get the service id
for each in root.iter('{http://www.ultipro.com/dataservices/bidata/2}ServiceId'):
    service_id = each.text

In [10]:
#Get the instance key
for each in root.iter('{http://www.ultipro.com/dataservices/bidata/2}InstanceKey'):
    instance_key = each.text

In [11]:
#Print the token
print(token)

800aa77a-55c2-4338-ab67-d2c17df0cbaf


In [12]:
#Print the service id
print(service_id)

dae1578e-72df-4278-9bb8-4cf1bb5b3ce9


In [13]:
#Print the instance key
print(instance_key)

2d046e0e-bbc4-448b-a8aa-67653ac41d8a


# Step 2: View the list of reports available

Now we will connect to the GetReportList endpoint, so that we can see the filepaths for all available reports

In [14]:
#Our endpoint
url="https://service5.ultipro.com/services/BIDataService"

#The below headers variable specifies that we are sending the request to a SOAP API
headers = {"content-type": "application/soap+xml"}

In [15]:
body = """   
<s:Envelope xmlns:s="http://www.w3.org/2003/05/soap-envelope" xmlns:a="http://www.w3.org/2005/08/addressing">

  <s:Header>

<a:Action s:mustUnderstand="1">http://www.ultipro.com/dataservices/bidata/2/IBIDataService/GetReportList</a:Action>

<a:To s:mustUnderstand="1">https://servicehost/services/BiDataService</a:To>

</s:Header>

  <s:Body>

  <GetReportList xmlns="http://www.ultipro.com/dataservices/bidata/2">

  <context xmlns:i="http://www.w3.org/2001/XMLSchema-instance">

<ServiceId>""" + service_id + """</ServiceId>

<ClientAccessKey>PLAB4</ClientAccessKey>

  <!-- GUID, unique per user session -->

<Token>""" + token + """</Token>

<Status>Ok</Status>

<StatusMessage i:nil="true" />

  <!-- GUID, unique per user session -->

<InstanceKey>""" + instance_key + """</InstanceKey>

</context>

</GetReportList>

</s:Body>

</s:Envelope> """

In [16]:
#
response = requests.post(url, headers=headers, data=body)
print (response)
print (response.text)

<Response [200]>
<s:Envelope xmlns:s="http://www.w3.org/2003/05/soap-envelope" xmlns:a="http://www.w3.org/2005/08/addressing"><s:Header><a:Action s:mustUnderstand="1">http://www.ultipro.com/dataservices/bidata/2/IBIDataService/GetReportListResponse</a:Action></s:Header><s:Body><GetReportListResponse xmlns="http://www.ultipro.com/dataservices/bidata/2"><GetReportListResult xmlns:i="http://www.w3.org/2001/XMLSchema-instance"><Reports><Report><ReportName>_Current Employee Deductions and Benefits</ReportName><ReportPath>/content/folder[@name='zzzCompany Folders']/folder[@name='Proliance Surgeons, Inc., P.S.']/folder[@name='UltiPro']/report[@name='_Current Employee Deductions and Benefits']</ReportPath></Report><Report><ReportName>2013-03-05T21:47:40.188Z</ReportName><ReportPath>/content/folder[@name='UltiPro BI Content']/folder[@name='UltiPro BI for Core HR and Payroll']/folder[@name='_UltiPro Delivered Packages']/package[@name='Open Enrollment Reporting Package']/agentDefinition[@name='Op

In [17]:
#Convert XML results to JSON
o = xmltodict.parse(response.text)
json_data = json.dumps(o)

In [18]:
#Turn the JSON data into a Python dictionary
a_dict = json.loads(json_data)
a_dict

{'s:Envelope': {'@xmlns:s': 'http://www.w3.org/2003/05/soap-envelope',
  '@xmlns:a': 'http://www.w3.org/2005/08/addressing',
  's:Header': {'a:Action': {'@s:mustUnderstand': '1',
    '#text': 'http://www.ultipro.com/dataservices/bidata/2/IBIDataService/GetReportListResponse'}},
  's:Body': {'GetReportListResponse': {'@xmlns': 'http://www.ultipro.com/dataservices/bidata/2',
    'GetReportListResult': {'@xmlns:i': 'http://www.w3.org/2001/XMLSchema-instance',
     'Reports': {'Report': [{'ReportName': '_Current Employee Deductions and Benefits',
        'ReportPath': "/content/folder[@name='zzzCompany Folders']/folder[@name='Proliance Surgeons, Inc., P.S.']/folder[@name='UltiPro']/report[@name='_Current Employee Deductions and Benefits']"},
       {'ReportName': '2013-03-05T21:47:40.188Z',
        'ReportPath': "/content/folder[@name='UltiPro BI Content']/folder[@name='UltiPro BI for Core HR and Payroll']/folder[@name='_UltiPro Delivered Packages']/package[@name='Open Enrollment Reporting

In [19]:
#Index the Python dictionary 
emp_dict = a_dict['s:Envelope']['s:Body']['GetReportListResponse']['GetReportListResult']['Reports']['Report']
emp_dict

[{'ReportName': '_Current Employee Deductions and Benefits',
  'ReportPath': "/content/folder[@name='zzzCompany Folders']/folder[@name='Proliance Surgeons, Inc., P.S.']/folder[@name='UltiPro']/report[@name='_Current Employee Deductions and Benefits']"},
 {'ReportName': '2013-03-05T21:47:40.188Z',
  'ReportPath': "/content/folder[@name='UltiPro BI Content']/folder[@name='UltiPro BI for Core HR and Payroll']/folder[@name='_UltiPro Delivered Packages']/package[@name='Open Enrollment Reporting Package']/agentDefinition[@name='Open Enrollment Session Available - NEW']/report[@name='2013-03-05T21:47:40.188Z']"},
 {'ReportName': '2020-10-26T18:25:32.678Z',
  'ReportPath': "/content/folder[@name='zzzCompany Folders']/folder[@name='Proliance Surgeons, Inc., P.S.']/folder[@name='UltiPro']/folder[@name='Customs']/agentDefinition[@name='Benefit Eligibility Alert']/report[@name='2020-10-26T18:25:32.678Z']"},
 {'ReportName': '2021 Allocation Report (1)',
  'ReportPath': "/content/folder[@name='zzzCo

In [20]:
#Normalize the dictionary, and convert into a pandas dataframe
df = pd.DataFrame.from_dict(pd.json_normalize(emp_dict), orient='columns')

df

ReportName  \
0   _Current Employee Deductions and Benefits   
1                    2013-03-05T21:47:40.188Z   
2                    2020-10-26T18:25:32.678Z   
3                  2021 Allocation Report (1)   
4                   401k Allocation Report V1   
..                                        ...   
72                            Test didactions   
73                           Test enrollments   
74    UNUM Benefit Billing By Provider Report   
75                        Active Benefits (1)   
76                    HSA Contribution Report   

                                           ReportPath  
0   /content/folder[@name='zzzCompany Folders']/fo...  
1   /content/folder[@name='UltiPro BI Content']/fo...  
2   /content/folder[@name='zzzCompany Folders']/fo...  
3   /content/folder[@name='zzzCompany Folders']/fo...  
4   /content/folder[@name='zzzCompany Folders']/fo...  
..                                                ...  
72  /content/folder[@name='zzzCompany Folders']/fo...  
73  /content/folder[@name='zzzCompany Folders']/fo...  
74  /content/folder[@name='zzzCompany Folders']/fo...  
75  /content/folder[@name='zzzCompany Folders']/fo...  
76  /content/folder[@name='zzzCompany Folders']/fo...  

[77 rows x 2 columns]

In [21]:
#View report names as a list
list(df['ReportName'])

['_Current Employee Deductions and Benefits',
 '2013-03-05T21:47:40.188Z',
 '2020-10-26T18:25:32.678Z',
 '2021 Allocation Report (1)',
 '401k Allocation Report V1',
 '401k Allocation Report V2',
 '401k Allocation Report V2_UKG',
 '401k Allocation Report V3_UKG',
 '401k Allocation Report V3_UKG v2',
 '401k Allocation Report V3_UKG v4',
 '5 Level Supervisors',
 'Active EE_DD List',
 'Allocated Hours FTE by Date',
 'Allocated Hours FTE by Month',
 'Annual Earnings',
 'Audit Report with Time vs Pay Matrix Tables',
 'Comp Project V3',
 'Configuration Validation',
 'Counts by Location',
 'Current Employee Deductions and Benefits',
 "David's Report",
 "David's Report V2",
 'Deduction list',
 'Deduction Pay History By Deduction For EmployeesUKG',
 'Deductions in Arrears V2',
 'Deferred Comp Wages and Hours_UKG',
 'Dependents by Employee and Plan test',
 'Document Category Report',
 'DSHS_New Hires',
 'Earning Codes Table',
 'Earnings Pay History By Earning Code For Employees_ULTI',
 'Earnings_

## Step 3: Use the ExecuteReport endpoint to get the report key

In [22]:
body = """   
  <s:Envelope xmlns:s="http://www.w3.org/2003/05/soap-envelope" xmlns:a="http://www.w3.org/2005/08/addressing">

  <s:Header>

<a:Action s:mustUnderstand="1">http://www.ultipro.com/dataservices/bidata/2/IBIDataService/ExecuteReport</a:Action>

<a:To s:mustUnderstand="1">https://servicehost/services/BiDataService</a:To>

</s:Header>

  <s:Body>

  <ExecuteReport xmlns="http://www.ultipro.com/dataservices/bidata/2">

  <request xmlns:i="http://www.w3.org/2001/XMLSchema-instance">

<ReportPath>/content/folder[@name='zzzCompany Folders']/folder[@name='Proliance Surgeons, Inc., P.S.']/folder[@name='UltiPro']/folder[@name='Export to SQL']/report[@name='Pre-Check Master']</ReportPath>

  <ReportParameters>

  <ReportParameter>

<Name>Month</Name>

<Value>1</Value>

<Required>false</Required>

<DataType>xsdDouble</DataType>

<MultiValued>true</MultiValued>

</ReportParameter>

</ReportParameters>

</request>

  <context xmlns:i="http://www.w3.org/2001/XMLSchema-instance">

<ServiceId>3ccd26d5-94b2-4c0f-b88a-5ccfbe3d7fb0</ServiceId>

<ClientAccessKey>PLAB4</ClientAccessKey>

<Token>""" + token + """</Token>

<Status>Ok</Status>

<StatusMessage i:nil="true" />

<InstanceKey>""" + instance_key + """</InstanceKey>

</context>

</ExecuteReport>

</s:Body>

</s:Envelope> """

In [23]:
#Get the report key
response = requests.post(url, headers=headers, data=body)
print (response)
print (response.text)

<Response [200]>
<s:Envelope xmlns:s="http://www.w3.org/2003/05/soap-envelope" xmlns:a="http://www.w3.org/2005/08/addressing"><s:Header><a:Action s:mustUnderstand="1">http://www.ultipro.com/dataservices/bidata/2/IBIDataService/ExecuteReportResponse</a:Action></s:Header><s:Body><ExecuteReportResponse xmlns="http://www.ultipro.com/dataservices/bidata/2"><ExecuteReportResult xmlns:i="http://www.w3.org/2001/XMLSchema-instance"><ReportKey>fa2c2b97-386b-4b27-9d60-5d157e01152d</ReportKey><ReportRetrievalUri>https://service5.ultipro.com/services/BIStreamingService</ReportRetrievalUri><Status>Success</Status><StatusMessage i:nil="true"/></ExecuteReportResult></ExecuteReportResponse></s:Body></s:Envelope>


In [24]:
#Write the response to a file
open("file.xml", "w").write(response.text)

687

In [25]:
#Open the file as an ElementTree object
tree = ET.parse('file.xml')
root = tree.getroot()

In [26]:
#Show all the elements in the tree
[elem.tag for elem in root.iter()]

['{http://www.w3.org/2003/05/soap-envelope}Envelope',
 '{http://www.w3.org/2003/05/soap-envelope}Header',
 '{http://www.w3.org/2005/08/addressing}Action',
 '{http://www.w3.org/2003/05/soap-envelope}Body',
 '{http://www.ultipro.com/dataservices/bidata/2}ExecuteReportResponse',
 '{http://www.ultipro.com/dataservices/bidata/2}ExecuteReportResult',
 '{http://www.ultipro.com/dataservices/bidata/2}ReportKey',
 '{http://www.ultipro.com/dataservices/bidata/2}ReportRetrievalUri',
 '{http://www.ultipro.com/dataservices/bidata/2}Status',
 '{http://www.ultipro.com/dataservices/bidata/2}StatusMessage']

In [27]:
#Get the report key from the "ReportKey" element in the tree
for each in root.iter('{http://www.ultipro.com/dataservices/bidata/2}ReportKey'):
    report_key = each.text

In [28]:
#View the report key
print(report_key)

fa2c2b97-386b-4b27-9d60-5d157e01152d


# Step 4: Use the RetrieveReport method to retrieve the report

In [29]:
#Our endpoint
url="https://service5.ultipro.com/services/BIStreamingService"

#The below headers variable specifies that we are sending the request to a SOAP API
headers = {"content-type": "application/soap+xml", 
           "charset": "utf-8",
           "SOAPAction": "http://www.ultipro.com/dataservices/bistream/2/IBIStreamService/RetrieveReport"}

In [30]:
body = """<s:Envelope xmlns:s="http://www.w3.org/2003/05/soap-envelope" xmlns:a="http://www.w3.org/2005/08/addressing">
	<s:Header>
		<a:Action s:mustUnderstand="1">http://www.ultipro.com/dataservices/bistream/2/IBIStreamService/RetrieveReport</a:Action>
		<h:ReportKey xmlns:h="http://www.ultipro.com/dataservices/bistream/2" xmlns="http://www.ultipro.com/dataservices/bistream/2">""" + report_key + """</h:ReportKey>
		<a:MessageID>urn:uuid:8332571f-3a89-4442-ac80-27195b397b4d</a:MessageID>
		<a:ReplyTo>
			<a:Address>http://www.w3.org/2005/08/addressing/anonymous</a:Address>
		</a:ReplyTo>
		<a:To s:mustUnderstand="1">https://service5.ultipro.com/services/BIStreamingService</a:To>
	</s:Header>
	<s:Body xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xmlns:xsd="http://www.w3.org/2001/XMLSchema">
		<RetrieveReportRequest xmlns="http://www.ultipro.com/dataservices/bistream/2"/>
	</s:Body>
</s:Envelope>"""

In [31]:
#Retrieve the report
response = requests.post(url, headers=headers, data=body)
print (response)
print (response.text)

<Response [200]>
<s:Envelope xmlns:s="http://www.w3.org/2003/05/soap-envelope" xmlns:a="http://www.w3.org/2005/08/addressing"><s:Header><a:Action s:mustUnderstand="1">http://www.ultipro.com/dataservices/bistream/2/IBIStreamService/RetrieveReportResponse</a:Action><h:Status xmlns:h="http://www.ultipro.com/dataservices/bistream/2">Completed</h:Status><h:StatusMessage i:nil="true" xmlns:h="http://www.ultipro.com/dataservices/bistream/2" xmlns:i="http://www.w3.org/2001/XMLSchema-instance"/><a:RelatesTo>urn:uuid:8332571f-3a89-4442-ac80-27195b397b4d</a:RelatesTo></s:Header><s:Body><StreamReportResponse xmlns="http://www.ultipro.com/dataservices/bistream/2"><ReportStream>...</ReportStream></StreamReportResponse></s:Body></s:Envelope>


In [32]:
#Write the response to a file
open("file.xml", "w").write(response.text)

2158936

In [33]:
#Open the file as an ElementTree object
tree = ET.parse('file.xml')
root = tree.getroot()

In [34]:
#Show all the elements in the tree
[elem.tag for elem in root.iter()]

['{http://www.w3.org/2003/05/soap-envelope}Envelope',
 '{http://www.w3.org/2003/05/soap-envelope}Header',
 '{http://www.w3.org/2005/08/addressing}Action',
 '{http://www.ultipro.com/dataservices/bistream/2}Status',
 '{http://www.ultipro.com/dataservices/bistream/2}StatusMessage',
 '{http://www.w3.org/2005/08/addressing}RelatesTo',
 '{http://www.w3.org/2003/05/soap-envelope}Body',
 '{http://www.ultipro.com/dataservices/bistream/2}StreamReportResponse',
 '{http://www.ultipro.com/dataservices/bistream/2}ReportStream']

In [35]:
#Get the token from the "Token" element in the tree
for each in root.iter('{http://www.ultipro.com/dataservices/bistream/2}ReportStream'):
    encoded_report = each.text 

In [36]:
#View the encoded report
encoded_report

'...'

The report is encoded in base 64, so we  need to decode it.

In [37]:
decoded = base64.b64decode(encoded_report).decode('utf-8')
decoded

'<?xml version="1.0" encoding="utf-8"?>\n<dataset  xmlns="http://developer.cognos.com/schemas/xmldata/1/"  xmlns:xs="http://www.w3.org/2001/XMLSchema-instance">\n<!--\n<dataset\n    xmlns="http://developer.cognos.com/schemas/xmldata/1/"\n    xmlns:xs="http://www.w3.org/2001/XMLSchema-instance"\n    xs:schemaLocation="http://developer.cognos.com/schemas/xmldata/1/ xmldata.xsd"\n>\n-->\n    <metadata>\n          <item name="Period Control Date" type="xs:dateTime"/>\n          <item name="Period Control" type="xs:string" length="20"/>\n          <item name="Period End Date" type="xs:dateTime"/>\n          <item name="Employee Number" type="xs:string" length="20"/>\n          <item name="Last, First MI" type="xs:string" length="132"/>\n          <item name="Location Code" type="xs:string" length="14"/>\n          <item name="Org Level 1 Code" type="xs:string" length="22"/>\n          <item name="Org Level 2 Code" type="xs:string" length="22"/>\n          <item name="Hourly Pay Rate" type="

In [38]:
#Convert XML results to JSON
o = xmltodict.parse(decoded)
json_data = json.dumps(o)
json_data

'{"dataset": {"@xmlns": "http://developer.cognos.com/schemas/xmldata/1/", "@xmlns:xs": "http://www.w3.org/2001/XMLSchema-instance", "metadata": {"item": [{"@name": "Period Control Date", "@type": "xs:dateTime"}, {"@name": "Period Control", "@type": "xs:string", "@length": "20"}, {"@name": "Period End Date", "@type": "xs:dateTime"}, {"@name": "Employee Number", "@type": "xs:string", "@length": "20"}, {"@name": "Last, First MI", "@type": "xs:string", "@length": "132"}, {"@name": "Location Code", "@type": "xs:string", "@length": "14"}, {"@name": "Org Level 1 Code", "@type": "xs:string", "@length": "22"}, {"@name": "Org Level 2 Code", "@type": "xs:string", "@length": "22"}, {"@name": "Hourly Pay Rate", "@type": "xs:decimal", "@scale": "6", "@precision": "38"}, {"@name": "Annual Salary", "@type": "xs:decimal", "@scale": "4", "@precision": "19"}, {"@name": "Job Code", "@type": "xs:string", "@length": "18"}, {"@name": "Job Title", "@type": "xs:string", "@length": "52"}, {"@name": "Total Hours

In [39]:
#Turn the JSON data into a Python dictionary
a_dict = json.loads(json_data)
a_dict

{'dataset': {'@xmlns': 'http://developer.cognos.com/schemas/xmldata/1/',
  '@xmlns:xs': 'http://www.w3.org/2001/XMLSchema-instance',
  'metadata': {'item': [{'@name': 'Period Control Date',
     '@type': 'xs:dateTime'},
    {'@name': 'Period Control', '@type': 'xs:string', '@length': '20'},
    {'@name': 'Period End Date', '@type': 'xs:dateTime'},
    {'@name': 'Employee Number', '@type': 'xs:string', '@length': '20'},
    {'@name': 'Last, First MI', '@type': 'xs:string', '@length': '132'},
    {'@name': 'Location Code', '@type': 'xs:string', '@length': '14'},
    {'@name': 'Org Level 1 Code', '@type': 'xs:string', '@length': '22'},
    {'@name': 'Org Level 2 Code', '@type': 'xs:string', '@length': '22'},
    {'@name': 'Hourly Pay Rate',
     '@type': 'xs:decimal',
     '@scale': '6',
     '@precision': '38'},
    {'@name': 'Annual Salary',
     '@type': 'xs:decimal',
     '@scale': '4',
     '@precision': '19'},
    {'@name': 'Job Code', '@type': 'xs:string', '@length': '18'},
    {'@

In [40]:
#Index the Python dictionary so we can retrieve the data
values_dict = a_dict['dataset']['data']['row']
values_dict

[{'value': ['2022-11-25T00:00:00',
   '202211251',
   '2022-11-19T00:00:00',
   '000000184',
   'Gonzalez, Sylvia R.',
   '007070',
   '007070',
   '001',
   '30',
   '62400',
   '110201',
   'Rev Cycle Collection Spec',
   '83.65',
   '0',
   '1909.48',
   '1909.48',
   '2509.5',
   '71.51',
   '528.51']},
 {'value': ['2022-11-25T00:00:00',
   '202211251',
   '2022-11-19T00:00:00',
   '000000226',
   'Swart, Tammy L.',
   '008040',
   '008040',
   '001',
   '27.91',
   '58052.8',
   '110131',
   'Scheduler',
   '80.88',
   '0',
   '1570.73',
   '1570.73',
   '2269.64',
   '245.49',
   '453.42']},
 {'value': ['2022-11-25T00:00:00',
   '202211251',
   '2022-11-19T00:00:00',
   '000000255',
   'Harmon, Kurt E.',
   '007700',
   '007700',
   '001',
   '17.341101',
   '36069.49',
   '300',
   'Physician',
   '0',
   '0',
   '9611.88',
   '9611.88',
   '11936.43',
   '0',
   '2324.55']},
 {'value': ['2022-11-25T00:00:00',
   '202211251',
   '2022-11-19T00:00:00',
   '000000273',
   'Clark, 

In [41]:
#Put the data into a list of lists
list_o_lst = []
for each in values_dict:
    list_o_lst.append(each['value'])

print(list_o_lst)

[['2022-11-25T00:00:00', '202211251', '2022-11-19T00:00:00', '000000184', 'Gonzalez, Sylvia R.', '007070', '007070', '001', '30', '62400', '110201', 'Rev Cycle Collection Spec', '83.65', '0', '1909.48', '1909.48', '2509.5', '71.51', '528.51'], ['2022-11-25T00:00:00', '202211251', '2022-11-19T00:00:00', '000000226', 'Swart, Tammy L.', '008040', '008040', '001', '27.91', '58052.8', '110131', 'Scheduler', '80.88', '0', '1570.73', '1570.73', '2269.64', '245.49', '453.42'], ['2022-11-25T00:00:00', '202211251', '2022-11-19T00:00:00', '000000255', 'Harmon, Kurt E.', '007700', '007700', '001', '17.341101', '36069.49', '300', 'Physician', '0', '0', '9611.88', '9611.88', '11936.43', '0', '2324.55'], ['2022-11-25T00:00:00', '202211251', '2022-11-19T00:00:00', '000000273', 'Clark, Jessica L.', '008040', '008040', '001', '24.5', '50960', '110101', 'Patient Services Rep', '83.45', '0', '1569.93', '1569.93', '2086.79', '171.51', '345.35'], ['2022-11-25T00:00:00', '202211251', '2022-11-19T00:00:00', '

In [42]:
#Turn the list of lists into a dataframe
df = pd.DataFrame(list_o_lst)
df

0          1                    2          3   \
0     2022-11-25T00:00:00  202211251  2022-11-19T00:00:00  000000184   
1     2022-11-25T00:00:00  202211251  2022-11-19T00:00:00  000000226   
2     2022-11-25T00:00:00  202211251  2022-11-19T00:00:00  000000255   
3     2022-11-25T00:00:00  202211251  2022-11-19T00:00:00  000000273   
4     2022-11-25T00:00:00  202211251  2022-11-19T00:00:00  000000290   
...                   ...        ...                  ...        ...   
2225  2022-11-25T00:00:00  202211251  2022-11-19T00:00:00  001008598   
2226  2022-11-25T00:00:00  202211251  2022-11-19T00:00:00  001008599   
2227  2022-11-25T00:00:00  202211251  2022-11-19T00:00:00  001008600   
2228  2022-11-25T00:00:00  202211251  2022-11-19T00:00:00  001008603   
2229  2022-11-25T00:00:00  202211251  2022-11-19T00:00:00  001008605   

                        4       5       6    7          8         9       10  \
0      Gonzalez, Sylvia R.  007070  007070  001         30     62400  110201   
1          Swart, Tammy L.  008040  008040  001      27.91   58052.8  110131   
2          Harmon, Kurt E.  007700  007700  001  17.341101  36069.49     300   
3        Clark, Jessica L.  008040  008040  001       24.5     50960  110101   
4            Kim, Helen H.  006000  006000  001  17.341101  36069.49     300   
...                    ...     ...     ...  ...        ...       ...     ...   
2225      Konkel, Karen A.  005300  005300  001         18         0  110331   
2226         Smith, Joy L.  002800  002800  001  72.115385    120000  410013   
2227  Swienty, Michelle A.  003400  003400  001       33.5     69680  120001   
2228     Watts, Natasha M.  001300  001300  001       19.5     20280  110001   
2229    Todd, Katherine L.  004400  004400  001  57.692308    120000  410002   

                             11     12       13       14       15        16  \
0     Rev Cycle Collection Spec  83.65        0  1909.48  1909.48    2509.5   
1                     Scheduler  80.88        0  1570.73  1570.73   2269.64   
2                     Physician      0        0  9611.88  9611.88  11936.43   
3          Patient Services Rep  83.45        0  1569.93  1569.93   2086.79   
4                     Physician      0        0        0        0         0   
...                         ...    ...      ...      ...      ...       ...   
2225                    PT Aide      9    148.9        0    148.9       162   
2226        Physician Assistant     32  1891.47        0  1891.47   2307.69   
2227                         RN  73.26  2036.81        0  2036.81    2515.6   
2228                         MA   2.75    49.28        0    49.28     53.62   
2229                       ARNP     40  1891.47        0  1891.47   2307.69   

          17       18  
0      71.51   528.51  
1     245.49   453.42  
2          0  2324.55  
3     171.51   345.35  
4          0        0  
...      ...      ...  
2225       0     13.1  
2226       0   416.22  
2227       0   478.79  
2228       0     4.34  
2229       0   416.22  

[2230 rows x 19 columns]

In [43]:
#Get the column names into a list
column_names_dict = a_dict['dataset']['metadata']['item']

column_names_lst = []

#Iterate through the dictionary to grab the column names, and append them to column_names_lst
for each in column_names_dict:

    #Grab the column name
    column = each['@name']

    #Turn the column name into lowercase
    column = column.lower()

    #Replace whitespace with underscore
    column = column.replace(' ', '_')

    #Append to new list
    column_names_lst.append(column)


print(column_names_lst)

['period_control_date', 'period_control', 'period_end_date', 'employee_number', 'last,_first_mi', 'location_code', 'org_level_1_code', 'org_level_2_code', 'hourly_pay_rate', 'annual_salary', 'job_code', 'job_title', 'total_hours', 'check_amount', 'direct_deposit_amount', 'net_amount', 'total_earning_amount', 'total_deduction_amount', 'total_taxes']


In [44]:
#Rename the columns in the dataframe, using column_names_lst
df.columns = column_names_lst 

#View the results
df.head(50)

period_control_date period_control      period_end_date employee_number  \
0   2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000000184   
1   2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000000226   
2   2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000000255   
3   2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000000273   
4   2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000000290   
5   2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000006001   
6   2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000010002   
7   2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000010010   
8   2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000010018   
9   2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000010048   
10  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000010074   
11  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000010082   
12  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000010092   
13  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000040010   
14  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000040012   
15  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000040014   
16  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000040015   
17  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000050002   
18  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000060009   
19  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000060055   
20  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000060056   
21  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000060063   
22  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000060070   
23  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000060080   
24  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000060084   
25  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000060115   
26  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000060124   
27  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000070114   
28  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000070231   
29  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000090024   
30  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000090076   
31  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000091026   
32  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000100016   
33  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000100032   
34  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000120022   
35  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000120023   
36  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000120046   
37  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000120048   
38  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000121023   
39  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000121037   
40  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000121054   
41  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000121058   
42  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000121060   
43  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000150023   
44  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000150067   
45  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000150076   
46  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000150100   
47  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000160001   
48  2022-11-25T00:00:00      202211251  2022-11-19T00:00:00       000160050   
49  2022-11-25T00:00:00      202211251  2022-11-19T00:

In [47]:
#Export the dataframe as a CSV file
df.to_csv('exported.csv')

In [48]:
df.loc[745]

period_control_date            2022-11-25T00:00:00
period_control                           202211251
period_end_date                2022-11-19T00:00:00
employee_number                          001004309
last,_first_mi                  Gillespie, Shannon
location_code                               003900
org_level_1_code                            003900
org_level_2_code               {'@xs:nil': 'true'}
hourly_pay_rate                                 30
annual_salary                                    0
job_code                                    110391
job_title                 Administrative Assistant
total_hours                                   23.5
check_amount                                     0
direct_deposit_amount                       612.28
net_amount                                  612.28
total_earning_amount                           705
total_deduction_amount                           0
total_taxes                                  92.72
Name: 745, dtype: object

# Step 5: Insert the data into BiSQL2

In [ ]:
import pyodbc
import sqlalchemy as sal
from sqlalchemy import create_engine

#Create SQL alchemy engine
engine = sal.create_engine('mssql+pyodbc://DC-BISQL01/BIData2?driver=SQL Server?Trusted_Connection=yes')
conn = engine.connect()
#Create our connection object
conn = pyodbc.connect('Driver={SQL Server};'
                      'Server=DC-BISQL01;'
                      'Database=BIData2;'
                      'Trusted_Connection=yes;')

cursor = conn.cursor()

#Create a table from our dataframe
df.to_sql('ZZ_TEST_PreCheck_Master', engine, if_exists='replace')


#Close the connection to BiData2
conn.close()


ProgrammingError: (pyodbc.ProgrammingError) ('Invalid parameter type.  param-index=8 param-type=dict', 'HY105')
[SQL: INSERT INTO [ZZ_TEST_PreCheck_Master] ([index], period_control_date, period_control, period_end_date, employee_number, [last,_first_mi], location_code, org_level_1_code, org_level_2_code, hourly_pay_rate, annual_salary, job_code, job_title, total_hours, check_amount, direct_deposit_amount, net_amount, total_earning_amount, total_deduction_amount, total_taxes) VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)]
[parameters: ((0, '2022-11-25T00:00:00', '202211251', '2022-11-19T00:00:00', '000000184', 'Gonzalez, Sylvia R.', '007070', '007070', '001', '30', '62400', '110201', 'Rev Cycle Collection Spec', '83.65', '0', '1909.48', '1909.48', '2509.5', '71.51', '528.51'), (1, '2022-11-25T00:00:00', '202211251', '2022-11-19T00:00:00', '000000226', 'Swart, Tammy L.', '008040', '008040', '001', '27.91', '58052.8', '110131', 'Scheduler', '80.88', '0', '1570.73', '

In [ ]:
#Close the connection to the API